### <a id='0'><h2 style="background-color:powderblue;border-radius:5px;text-align:center;padding:7px;color:steelblue;font-family:Garamond;">Personality Detection Model</h2></a>

<h3>Overview:</h3>
I have structured the data modelling into 5 key sections. Below, I will share with you the steps I took together with insights for each section.

1. Introduction
2. Data Understanding
3. Data Preparation
4. Exploratary Data Analysis
5. Modelling,Evaluation and Prediction

### <a id='1'><h2 style="background-color:lightblue;border-radius:5px;text-align:center;padding:7px;color:white;"><font color="white">1. Introduction</h2></a>

#### Basis of Prediction

I would be basing my prediction and analysis on the 16 big personalities from the Myers–Briggs Type Indicator (MBTI), describe the preferences of an individual in four dimensions and these basic dimensions combine into one of 16 different personality types. The four dimensions include Extroversion–Introversion (E–I), Sensation–Intuition (S–N), Thinking–Feeling (T–F), and Judgment–Perception (J–P). There are two types of personalities in each dimension. 

Using the Myers–Briggs Type Indicator®, preferences of an individual are categorized into four dimensions, and these categories represent 16 different types of personality based on the Myers–Briggs Type Indicator®. There are 16 personality types individuals can develop based on the interaction between their preferences.

d
<img src="https://advertisingrow.com/wp-content/uploads/2019/09/Infographic-Myers-Briggs-Personality-Types.jpg">

<img src="https://assets.weforum.org/editor/3kl2hZ0guKiGPhEcTpiX794PB-1R9j3OlOfQtO8N1rE.JPG">

#### Methodology

This would be how I would be performing my prediction

1. <b>Exploring MBTI dataset on Kaggle</b>
2. <b>Training and Testing of Model on MBTI dataset</b>
3. <b>Application of model on Reviews and Tips Text Column</b>

#### Package Imports

In [0]:
pip install nltk

Python interpreter will be restarted.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-05e35396-b2fb-41c2-aec1-74091cde0cac/bin/python -m pip install --upgrade pip' command.
Python interpreter will be restarted.


In [0]:
pip install wordcloud

Python interpreter will be restarted.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-05e35396-b2fb-41c2-aec1-74091cde0cac/bin/python -m pip install --upgrade pip' command.
Python interpreter will be restarted.


In [0]:
pip install keras

Python interpreter will be restarted.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-05e35396-b2fb-41c2-aec1-74091cde0cac/bin/python -m pip install --upgrade pip' command.
Python interpreter will be restarted.


In [0]:
pip install tensorflow

Python interpreter will be restarted.
  Created wheel for termcolor: filename=termcolor-1.1.0-py3-none-any.whl size=4829 sha256=913dab37e60409de044ca439c54fc38e91ee756e6c239ad52aaae46091c6bf11
  Stored in directory: /root/.cache/pip/wheels/a0/16/9c/5473df82468f958445479c59e784896fa24f4a5fc024b0f501
Successfully built termcolor
  Attempting uninstall: numpy
    Found existing installation: numpy 1.19.2
    Not uninstalling numpy at /databricks/python3/lib/python3.8/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-05e35396-b2fb-41c2-aec1-74091cde0cac
    Can't uninstall 'numpy'. No files were found to uninstall.
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-05e35396-b2fb-41c2-aec1-74091cde0cac/bin/python -m pip install --upgrade pip' command.
Python interpreter will be restarted.


In [0]:

import nltk
nltk.download('wordnet')
nltk.download('omw-1.4')


[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Unzipping corpora/omw-1.4.zip.
Out[1]: True

In [0]:

# Packages

from keras.preprocessing import sequence, text
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation
from keras.layers import Embedding, LSTM
from keras.layers import Conv1D, Flatten, MaxPooling1D

import pandas as pd
import numpy as np
import string
from nltk.stem import WordNetLemmatizer
from nltk.corpus import stopwords


# Visualisation

import matplotlib.pyplot as plt 
%matplotlib inline
import seaborn as sns
from wordcloud import WordCloud, STOPWORDS


# Model Building

    #classifiers
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.ensemble import AdaBoostClassifier

    #vectorizers
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer

    #training features
from sklearn.model_selection import cross_val_score, train_test_split
from sklearn.model_selection import GridSearchCV

    #performance measures
from sklearn.metrics import accuracy_score,log_loss
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.metrics import make_scorer

    #filter future warnings
#two futre warnings occured multiple times when running cross validation and GridSearchCV have been removed
#FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
#FutureWarning: The default value of cv will change from 3 to 5 in version 0.22
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

### <a id='2'><h2 style="background-color:lightblue;border-radius:5px;text-align:center;padding:7px;color:white;"><font color="white">2. MBTI Dataset Understanding</h2></a>

In [0]:
mbti_DF = (spark.read
  .option("inferSchema", True)
  .csv("/FileStore/tables/Project_Data_Extract/Personality_Dashboard/mbti_1.csv"))
mbti_pdf=mbti_DF.toPandas()
mbti_pdf=mbti_pdf.rename(columns={'_c0': 'type', '_c1': 'posts'})
mbti_pdf=mbti_pdf.iloc[1:]
mbti_pdf

type 
 posts 
 
 
 
 
 1 
 INFJ 
 'http://www.youtube.com/watch?v=qsXHcwe3krw|||... 
 
 
 2 
 ENTP 
 'I'm finding the lack of me in these posts ver... 
 
 
 3 
 INTP 
 'Good one _____ https://www.youtube.com/wat... 
 
 
 4 
 INTJ 
 'Dear INTP, I enjoyed our conversation the o... 
 
 
 5 
 ENTJ 
 'You're fired.|||That's another silly misconce... 
 
 
 ... 
 ... 
 ... 
 
 
 8671 
 ISFP 
 'https://www.youtube.com/watch?v=t8edHB_h908||... 
 
 
 8672 
 ENFP 
 'So...if this thread already exists someplace ... 
 
 
 8673 
 INTP 
 'So many questions when i do these things. I ... 
 
 
 8674 
 INFP 
 'I am very conflicted right now when it comes ... 
 
 
 8675 
 INFP 
 'It has been too long since I have been on per... 
 
 
 
 8675 rows × 2 columns

In [0]:
mbti_pdf.shape

Out[4]: (8675, 2)

In [0]:
mbti_pdf.dtypes

Out[5]: type     object
posts    object
dtype: object

This dataset consists of <b>2 rows- MBTI type and the posts containing text</b>

### <a id='3'><h2 style="background-color:lightblue;border-radius:5px;text-align:center;padding:7px;color:white;"><font color="white">3. MBTI Dataset Preparation</h2></a>

#### Removing Delimeters

In [0]:
def remove_delimiters (post):
    new = post.replace('|||',' ')
    return ' '.join(new.split())

mbti_pdf['posts'] = mbti_pdf['posts'].apply(remove_delimiters)

#### Removing URLs

In [0]:
## Remove urls
pattern_url = r'http[s]?://(?:[A-Za-z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9A-Fa-f][0-9A-Fa-f]))+'
subs_url = r'url-web'

#apply to train set
mbti_pdf['posts'] = mbti_pdf['posts'].replace(to_replace = pattern_url, value = subs_url, regex = True)


#### Convert words to lowercase

In [0]:
mbti_pdf['posts'] = mbti_pdf['posts'].str.lower()

#### Removing Punctuations and Numbers

In [0]:
def remove_punctuation(post):
    punc_numbers = string.punctuation + '0123456789'
    return ''.join([l for l in post if l not in punc_numbers])

mbti_pdf['posts'] = mbti_pdf['posts'].apply(remove_punctuation)

#### Lemmatization

In [0]:
# Lematise posts
lemmatizer = WordNetLemmatizer()
mbti_pdf['lemmatized_text'] = [' '.join([lemmatizer.lemmatize(word) for word in text.split(' ')])for text in mbti_pdf['posts']]

In [0]:
mbti_pdf['type'].unique()

Out[11]: array(['INFJ', 'ENTP', 'INTP', 'INTJ', 'ENTJ', 'ENFJ', 'INFP', 'ENFP',
       'ISFP', 'ISTP', 'ISFJ', 'ISTJ', 'ESTP', 'ESFP', 'ESTJ', 'ESFJ'],
      dtype=object)

In [0]:
mbti_pdf

type 
 posts 
 lemmatized_text 
 
 
 
 
 1 
 INFJ 
 urlweb urlweb enfp and intj moments urlweb spo... 
 urlweb urlweb enfp and intj moment urlweb spor... 
 
 
 2 
 ENTP 
 im finding the lack of me in these posts very ... 
 im finding the lack of me in these post very a... 
 
 
 3 
 INTP 
 good one urlweb of course to which i say i kn... 
 good one urlweb of course to which i say i kn... 
 
 
 4 
 INTJ 
 dear intp i enjoyed our conversation the other... 
 dear intp i enjoyed our conversation the other... 
 
 
 5 
 ENTJ 
 youre fired thats another silly misconception ... 
 youre fired thats another silly misconception ... 
 
 
 ... 
 ... 
 ... 
 ... 
 
 
 8671 
 ISFP 
 urlweb ixfp just because i always think of cat... 
 urlweb ixfp just because i always think of cat... 
 
 
 8672 
 ENFP 
 soif this thread already exists someplace else... 
 soif this thread already exists someplace else... 
 
 
 8673 
 INTP 
 so many questions when i do these things i wou... 
 so many question when i do these thing i would... 
 
 
 8674 
 INFP 
 i am very conflicted right now when it comes t... 
 i am very conflicted right now when it come to... 
 
 
 8675 
 INFP 
 it has been too long since i have been on pers... 
 it ha been too long since i have been on perso... 
 
 
 
 8675 rows × 3 columns

### <a id='4'><h2 style="background-color:lightblue;border-radius:5px;text-align:center;padding:7px;color:white;"><font color="white">4. MBTI EDA</h2></a>

### <a id='5'><h2 style="background-color:lightblue;border-radius:5px;text-align:center;padding:7px;color:white;"><font color="white">5. MBTI Modelling, Evaluation & Prediction</h2></a>

#### Preparing Data for modelling

In [0]:
mbti_pdf['Is E'] = mbti_pdf['type'].apply(lambda x: x[0] == 'E').astype('int')
mbti_pdf['Is N'] = mbti_pdf['type'].apply(lambda x: x[1] == 'N').astype('int')
mbti_pdf['Is T'] = mbti_pdf['type'].apply(lambda x: x[2] == 'T').astype('int')
mbti_pdf['Is J'] = mbti_pdf['type'].apply(lambda x: x[3] == 'J').astype('int')

mbti_pdf

type 
 posts 
 lemmatized_text 
 Is E 
 Is N 
 Is T 
 Is J 
 
 
 
 
 1 
 INFJ 
 urlweb urlweb enfp and intj moments urlweb spo... 
 urlweb urlweb enfp and intj moment urlweb spor... 
 0 
 1 
 0 
 1 
 
 
 2 
 ENTP 
 im finding the lack of me in these posts very ... 
 im finding the lack of me in these post very a... 
 1 
 1 
 1 
 0 
 
 
 3 
 INTP 
 good one urlweb of course to which i say i kn... 
 good one urlweb of course to which i say i kn... 
 0 
 1 
 1 
 0 
 
 
 4 
 INTJ 
 dear intp i enjoyed our conversation the other... 
 dear intp i enjoyed our conversation the other... 
 0 
 1 
 1 
 1 
 
 
 5 
 ENTJ 
 youre fired thats another silly misconception ... 
 youre fired thats another silly misconception ... 
 1 
 1 
 1 
 1 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 8671 
 ISFP 
 urlweb ixfp just because i always think of cat... 
 urlweb ixfp just because i always think of cat... 
 0 
 0 
 0 
 0 
 
 
 8672 
 ENFP 
 soif this thread already exists someplace else... 
 soif this thread already exists someplace else... 
 1 
 1 
 0 
 0 
 
 
 8673 
 INTP 
 so many questions when i do these things i wou... 
 so many question when i do these thing i would... 
 0 
 1 
 1 
 0 
 
 
 8674 
 INFP 
 i am very conflicted right now when it comes t... 
 i am very conflicted right now when it come to... 
 0 
 1 
 0 
 0 
 
 
 8675 
 INFP 
 it has been too long since i have been on pers... 
 it ha been too long since i have been on perso... 
 0 
 1 
 0 
 0 
 
 
 
 8675 rows × 7 columns

#### Duplicate data by 10 times

In [0]:
frames=[mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf,mbti_pdf]
mbti_pdf=pd.concat(frames)
mbti_pdf.reset_index(inplace=True)
mbti_pdf.drop(['index'],axis=1,inplace=True)




In [0]:
mbti_pdf

type 
 posts 
 lemmatized_text 
 Is E 
 Is N 
 Is T 
 Is J 
 
 
 
 
 0 
 INFJ 
 urlweb urlweb enfp and intj moments urlweb spo... 
 urlweb urlweb enfp and intj moment urlweb spor... 
 0 
 1 
 0 
 1 
 
 
 1 
 ENTP 
 im finding the lack of me in these posts very ... 
 im finding the lack of me in these post very a... 
 1 
 1 
 1 
 0 
 
 
 2 
 INTP 
 good one urlweb of course to which i say i kn... 
 good one urlweb of course to which i say i kn... 
 0 
 1 
 1 
 0 
 
 
 3 
 INTJ 
 dear intp i enjoyed our conversation the other... 
 dear intp i enjoyed our conversation the other... 
 0 
 1 
 1 
 1 
 
 
 4 
 ENTJ 
 youre fired thats another silly misconception ... 
 youre fired thats another silly misconception ... 
 1 
 1 
 1 
 1 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 95420 
 ISFP 
 urlweb ixfp just because i always think of cat... 
 urlweb ixfp just because i always think of cat... 
 0 
 0 
 0 
 0 
 
 
 95421 
 ENFP 
 soif this thread already exists someplace else... 
 soif this thread already exists someplace else... 
 1 
 1 
 0 
 0 
 
 
 95422 
 INTP 
 so many questions when i do these things i wou... 
 so many question when i do these thing i would... 
 0 
 1 
 1 
 0 
 
 
 95423 
 INFP 
 i am very conflicted right now when it comes t... 
 i am very conflicted right now when it come to... 
 0 
 1 
 0 
 0 
 
 
 95424 
 INFP 
 it has been too long since i have been on pers... 
 it ha been too long since i have been on perso... 
 0 
 1 
 0 
 0 
 
 
 
 95425 rows × 7 columns

In [0]:
X=mbti_pdf['lemmatized_text']
y=mbti_pdf['type']

In [0]:
# One Hot encoding on the dataset output classes 
y = pd.DataFrame(mbti_pdf[['Is E','Is N','Is T', 'Is J']])
x_train,x_test,y_train,y_test = train_test_split(mbti_pdf['lemmatized_text'], y,random_state=0)


In [0]:
vocab_size = 1000
max_len =1000
batch_size = 32
embedding_dims =10
filters = 16
ker_size = 3 # kernel size
hidden_dims = 250
epochs = 10

In [0]:
from keras.preprocessing import sequence, text
tokenizer = text.Tokenizer(num_words=vocab_size)
tokenizer.fit_on_texts(x_train)

In [0]:
x_train = tokenizer.texts_to_matrix(x_train)
x_test = tokenizer.texts_to_matrix(x_test)

In [0]:
x_train = sequence.pad_sequences(x_train,maxlen=max_len)
x_test = sequence.pad_sequences(x_test,maxlen=max_len)

#### Building CNN model to predict personalities from text

In [0]:
model = Sequential()
# First we add an embedding layer 
model.add(Embedding(vocab_size,embedding_dims,input_length=max_len)) 
# Adding a 1D convolutional Layer
model.add(Conv1D(filters, ker_size, padding='valid', activation='relu'))
# Max Pooling the Convolutions
model.add(MaxPooling1D())
# Again Computing the Convolutions
model.add(Flatten())
model.add(Dense(hidden_dims, activation='relu'))
model.add(Dense(4, activation='sigmoid'))
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])


In [0]:
# Training the modeL
model.fit(x_train,y_train, batch_size=batch_size, epochs=10, validation_data=(x_test, y_test))

Epoch 1/10
2237/2237 [==============================] - 107s 47ms/step - loss: 0.2819 - accuracy: 0.6154 - val_loss: 0.0747 - val_accuracy: 0.5846
Epoch 2/10
2237/2237 [==============================] - 104s 47ms/step - loss: 0.0268 - accuracy: 0.6352 - val_loss: 0.0255 - val_accuracy: 0.6865
Epoch 3/10
2237/2237 [==============================] - 110s 49ms/step - loss: 0.0126 - accuracy: 0.6337 - val_loss: 0.0040 - val_accuracy: 0.6383
Epoch 4/10
2237/2237 [==============================] - 112s 50ms/step - loss: 0.0093 - accuracy: 0.6387 - val_loss: 0.0057 - val_accuracy: 0.6524
Epoch 5/10
2237/2237 [==============================] - 104s 47ms/step - loss: 0.0077 - accuracy: 0.6421 - val_loss: 0.0079 - val_accuracy: 0.6511
Epoch 6/10
2237/2237 [==============================] - 104s 47ms/step - loss: 0.0057 - accuracy: 0.6397 - val_loss: 0.0037 - val_accuracy: 0.6358
Epoch 7/10
2237/2237 [==============================] - 105s 47ms/step - loss: 0.0054 - accuracy: 0.6401 - val_loss: 0

In [0]:
model.evaluate(x_test,y_test)[1]*100  # Accuracy of the model

746/746 [==============================] - 9s 13ms/step - loss: 0.0016 - accuracy: 0.6585
Out[24]: 65.8465027809143

In [0]:

model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 embedding (Embedding)       (None, 1000, 10)          10000     
                                                                 
 conv1d (Conv1D)             (None, 998, 16)           496       
                                                                 
 max_pooling1d (MaxPooling1D  (None, 499, 16)          0         
 )                                                               
                                                                 
 flatten (Flatten)           (None, 7984)              0         
                                                                 
 dense (Dense)               (None, 250)               1996250   
                                                                 
 dense_1 (Dense)             (None, 4)                 1004      
                                                        

In [0]:
def predict_personality(text):
    text= pd.Series(text)
    text= tokenizer.texts_to_matrix(text)
    text= sequence.pad_sequences(text)
    l = model.predict(text)
    a,b= l[0][0]*(1/1999), l[0][1]*(1/1197)
    a = a/(1/1999)+(1/1197)
    b = b/(1/1999)+(1/1197)
    l = [a,b,l[0][2],l[0][3]]
    s=''
    if l[0] >0.5:
        s +='E'
    else:
        s+='I'
    if l[1] >0.5:
        s+='S'
    else:
        s+='N'
    if l[2] >0.5:
        s+='T'
    else:
        s+='F'
    if l[3] >0.5:
        s+='J'
    else:
        s+='P'
    return s




In [0]:
s ='Idealistic, loyal to their values and to people who are important to them. Want an external life that is congruent with their values. Curious, quick to see possibilities, can be catalysts for implementing ideas. Seek to understand people and to help them fulfill their potential. Adaptable, flexible, and accepting unless a value is threatened.'

print(predict_personality(s))

ISTP


#### Apply model to specicfic business

In [0]:
# accessing cleaned file
reviewsDF = (spark.read
  .option("inferSchema", True).json("/FileStore/tables/Project_Data_Extract/Reviews_Final.json"))
spark.conf.set("spark.sql.execution.arrow.enabled", "false") 
reviews_pdf=reviewsDF.toPandas()

In [0]:
reviews_pdf['personality']=reviews_pdf['text_syntatics_cleaned'].apply(predict_personality)

In [0]:
reviews_pdf

Aspect 
 Aspect Keywords 
 Aspect Sentiment 
 Food_Entities 
 Overall Aspect 
 business_id 
 cool 
 date 
 funny 
 month 
 stars 
 text_syntatics_cleaned 
 useful 
 personality 
 
 
 
 
 0 
 [FOOD#QUALITY, RESTAURANT#GENERAL, FOOD#QUALIT... 
 [grubhub order sent chopstick soy sauce, would... 
 [neutral, neutral, neutral, negative, negative... 
 [chopstick soy sauce] 
 RESTAURANT#GENERAL 
 dZh2u96vAN8pdHmiwcpXdw 
 0 
 3/7/2019 
 1 
 3 
 1 
 ordered grubhubstaying hotel indicated order s... 
 0 
 ISTJ 
 
 
 1 
 [RESTAURANT#GENERAL, RESTAURANT#GENERAL, AMBIE... 
 [pleasant surprise, burn time, planned great a... 
 [positive, neutral, positive, positive, positive] 
 [] 
 SERVICE#GENERAL 
 dZh2u96vAN8pdHmiwcpXdw 
 0 
 2/15/2019 
 0 
 2 
 5 
 pleasant surprise whatever stopped ra burn tim... 
 0 
 ISTP 
 
 
 2 
 [SERVICE#GENERAL, RESTAURANT#GENERAL, RESTAURA... 
 [always super, clean come time, always good, e... 
 [positive, positive, positive, neutral, neutra... 
 [food yummy hater] 
 FOOD#QUALITY 
 dZh2u96vAN8pdHmiwcpXdw 
 0 
 3/22/2019 
 0 
 3 
 5 
 love place atmosphere nice always super clean ... 
 0 
 INTJ 
 
 
 3 
 [RESTAURANT#GENERAL, FOOD#QUALITY, FOOD#QUALITY] 
 [avocadofresh rice, loose small, portion roll ... 
 [positive, negative, neutral] 
 [miso soup flavor tofu] 
 FOOD#QUALITY 
 dZh2u96vAN8pdHmiwcpXdw 
 0 
 2/23/2019 
 0 
 2 
 1 
 fish avocadofresh riceloose small portion roll... 
 1 
 ISTP 
 
 
 4 
 [RESTAURANT#GENERAL, SERVICE#GENERAL, RESTAURA... 
 [experience meal, card split bill couple minut... 
 [neutral, neutral, negative, neutral, neutral,... 
 [] 
 SERVICE#GENERAL 
 dZh2u96vAN8pdHmiwcpXdw 
 0 
 3/17/2019 
 0 
 3 
 2 
 girlfriend came two week ago quite experience ... 
 3 
 ISTJ 
 
 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 ... 
 
 
 436 
 [FOOD#QUALITY, FOOD#STYLE_OPTIONS, FOOD#QUALIT... 
 [roll goyoza oz rice, tiny roll, taste old man... 
 [neutral, neutral, neutral, neutral, neutral, ... 
 [roll goyoza oz rice roll sauce] 
 SERVICE#GENERAL 
 s7baMoiG1821_3NblCfK6w 
 0 
 10/4/2020 
 0 
 10 
 1 
 terrible ordered roll goyoza oz rice got tiny ... 
 0 
 ISTJ 
 
 
 437 
 [RESTAURANT#GENERAL, RESTAURANT#GENERAL, FOOD#... 
 [least time, must say, sushi ok host, rude ser... 
 [neutral, neutral, positive, negative, neutral... 
 [] 
 SERVICE#GENERAL 
 s7baMoiG1821_3NblCfK6w 
 0 
 11/1/2020 
 0 
 11 
 2 
 whatever least time must say sushi ok host sta... 
 0 
 ISTP 
 
 
 438 
 [SERVICE#GENERAL, SERVICE#GENERAL, SERVICE#GEN... 
 [table reservation, minute service, server nev... 
 [neutral, neutral, neutral, neutral, neutral, ... 
 [] 
 SERVICE#GENERAL 
 s7baMoiG1821_3NblCfK6w 
 0 
 10/25/2020 
 0 
 10 
 2 
 whatever sorry_about_that table reservation wa... 
 0 
 ISFP 
 
 
 439 
 [RESTAURANT#GENERAL, FOOD#QUALITY, RESTAURANT#... 
 [place dozen time, really great, experience gr... 
 [neutral, positive, positive, neutral, neutral... 
 [] 
 RESTAURANT#GENERAL 
 s7baMoiG1821_3NblCfK6w 
 0 
 11/9/2020 
 0 
 11 
 5 
 I visited place dozen time past year I really ... 
 0 
 ISFP 
 
 
 440 
 [FOOD#QUALITY, FOOD#QUALITY, SERVICE#GENERAL, ... 
 [foodbland basic nothing, place sushi, decent ... 
 [neutral, neutral, neutral, neutral] 
 [] 
 SERVICE#GENERAL 
 s7baMoiG1821_3NblCfK6w 
 0 
 11/1/2020 
 0 
 11 
 2 
 foodbland basic nothing special place sushidec... 
 0 
 ISFJ 
 
 
 
 441 rows × 14 columns

In [0]:
#tips_pdf['Emotion']=tips_pdf['text_syntatics_cleaned'].apply(predict_emotion)
from pyspark.sql import SparkSession
#Create PySpark SparkSession
spark = SparkSession.builder \
    .master("local[1]") \
    .appName("SparkByExamples.com") \
    .getOrCreate()
reviewsDF=spark.createDataFrame(reviews_pdf) 
reviewsDF.coalesce(1).write.mode('overwrite').format('json').save("/FileStore/tables/Project_Data_Extract/Reviews_Final.json")

In [0]:
tipsDF = (spark.read
  .option("inferSchema", True)
  .json("/FileStore/tables/Project_Data_Extract/dataset_tips.json"))

tips_pdf=tipsDF.toPandas()
tips_pdf=tips_pdf[tips_pdf['business_id'].isin(['s7baMoiG1821_3NblCfK6w','dZh2u96vAN8pdHmiwcpXdw'])]

In [0]:
tips_pdf['personality']=tips_pdf['text'].apply(predict_personality)

In [0]:
#tips_pdf['Emotion']=tips_pdf['text_syntatics_cleaned'].apply(predict_emotion)
from pyspark.sql import SparkSession
#Create PySpark SparkSession
spark = SparkSession.builder \
    .master("local[1]") \
    .appName("SparkByExamples.com") \
    .getOrCreate()
DF=spark.createDataFrame(tips_pdf) 
DF.coalesce(1).write.mode('overwrite').format('json').save("/FileStore/tables/Project_Data_Extract/Tips_Final.json")